In [1]:
import json
import pandas as pd

with open('conversations.json', 'r') as f:
    data = json.load(f)

convos = data

/Users/paul/opt/anaconda3/lib/python3.9/site-packages/pandas/core/computation/expressions.py:21: UserWarning: Pandas requires version '2.8.4' or newer of 'numexpr' (version '2.8.3' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED
/Users/paul/opt/anaconda3/lib/python3.9/site-packages/pandas/core/arrays/masked.py:61: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


In [2]:
rows: list[dict] = []
for convo in convos:
    convo_id = convo.get('id') or convo.get('conversation_id')
    
    # Handle the new mapping structure
    if 'mapping' in convo and isinstance(convo['mapping'], dict):
        messages = []
        for node_id, node in convo['mapping'].items():
            if node.get('message') and isinstance(node['message'], dict):
                messages.append(node['message'])
    else:
        # Fallback for old format
        messages = (
            convo.get('mapping', {}).values() if 'mapping' in convo else convo.get('messages', [])
        )
    
    for m in messages:
        if not isinstance(m, dict):
            continue
            
        role = (
            m.get('author', {}).get('role') if 'author' in m else m.get('role', '')
        )
        
        # More robust content extraction for new format
        content = ''
        if m.get('content') and isinstance(m.get('content'), dict):
            content_obj = m.get('content', {})
            if content_obj.get('content_type') == 'text' and content_obj.get('parts'):
                content = content_obj.get('parts', [''])[0] or ''
            elif isinstance(content_obj.get('text'), str):
                content = content_obj.get('text', '')
        elif m.get('text'):
            content = m.get('text')
        elif m.get('message') and isinstance(m.get('message'), dict):
            message_content = m.get('message', {}).get('content', {})
            if isinstance(message_content, dict) and message_content.get('parts'):
                content = message_content.get('parts', [''])[0] or ''
            elif isinstance(message_content, str):
                content = message_content
        elif isinstance(m.get('content'), str):
            content = m.get('content', '')
        
        ts = m.get('create_time') or m.get('timestamp')
        if ts is None:
            continue
        rows.append(
            {
                'conversation_id': convo_id,
                'role': role,
                'content': content,
                'timestamp': float(ts),
            }
        )

In [7]:
df = pd.DataFrame(rows)
df['dt'] = pd.to_datetime(df['timestamp'], unit='s')

user_df = df[df['role'] == 'user'].copy()
user_df['date'] = user_df['dt'].dt.date
user_df['word_count'] = user_df['content'].str.split().str.len()

user_df





conversation_id  role  \
0      685c314b-78f4-8011-bace-de24228b8f5a  user   
9      685c314b-78f4-8011-bace-de24228b8f5a  user   
15     685c2e1d-1e08-8011-bb0e-a6cf53d3c2fc  user   
29     685bd4ab-a248-8011-a310-747581d54f88  user   
55     685bd322-2d18-8011-90a5-8ce5514e7ca0  user   
...                                     ...   ...   
17529  673c79f5-6fb4-8011-99e5-79c848196936  user   
17531  673c727f-8c34-8011-ac08-4202c04acd04  user   
17534  673c727f-8c34-8011-ac08-4202c04acd04  user   
17536  673c727f-8c34-8011-ac08-4202c04acd04  user   
17538  673c727f-8c34-8011-ac08-4202c04acd04  user   

                                                 content     timestamp  \
0      I am planning on building a web app that lets ...  1.750872e+09   
9               Get me started on the MVP with Streamlit  1.750873e+09   
15     In what store Berlin can I buy the FlipBelt Zi...  1.750872e+09   
29     What’s the best storage solution for my phone ...  1.750849e+09   
55                                                        1.750848e+09   
...                                                  ...           ...   
17529  > crsp17_18 = crsp.sample %>%\n+   filter(date...  1.732017e+09   
17531  why is there a difference?: > # Initialize por...  1.732015e+09   
17534                                         cov_m[i,j]  1.732015e+09   
17536  explain this: (This is equivalent to t(weights...  1.732015e+09   
17538                                   explain the code  1.732015e+09   

                                 dt        date  word_count  
0     2025-06-25 17:26:34.950000048  2025-06-25         192  
9     2025-06-25 17:30:27.760999918  2025-06-25           8  
15    2025-06-25 17:13:00.697999954  2025-06-25          10  
29    2025-06-25 10:51:23.445375919  2025-06-25          51  
55    2025-06-25 10:44:49.749819040  2025-06-25           0  
...                             ...         ...         ...  
17529 2024-11-19 11:47:16.838457108  2024-11-19          66  
17531 2024-11-19 11:11:59.861709118  2024-11-19         198  
17534 2024-11-19 11:15:24.467998981  2024-11-19           1  
17536 2024-11-19 11:23:13.613331079  2024-11-19          11  
17538 2024-11-19 11:24:40.661813974  2024-11-19           3  

[5480 rows x 7 columns]

In [30]:
# length of the first message in words
len(user_df['content'].iloc[0].split())

192

In [21]:
messages_string = ''
conversation_id = user_df['conversation_id'].iloc[0]
for i in range(len(user_df)):
    if user_df['conversation_id'].iloc[i] != conversation_id:
        messages_string += '\n\n'
        conversation_id = user_df['conversation_id'].iloc[i]
    messages_string += user_df['content'].iloc[i] + '\n'
messages_string


'I am planning on building a web app that lets a user see his ChatGPT statistics kind of like Spotify Wrapped. I want the user to be able to upload all of their past conversations and then get detailed analytics on them. At a latter stage I might also want to save their chats with their consent of course but for now I just want to build the web app that after uploading the past conversation with chatgpt will display interesting metrics. First of I want to display metrics the are easily computable like Average request per day, average conversation length, average requests in words, total number of requests, most number of request on one day… I also want to display metrics that use an LLM as a back bone to figure out the most touched topics, likely interests of the user, guesses on his/her profession and paint a likely picture of them with dalle. Help me turn this vision into a reality by first advising me on the tech stack. I want to build this app as fast as possible and want to use a 

In [24]:
print(messages_string)

I am planning on building a web app that lets a user see his ChatGPT statistics kind of like Spotify Wrapped. I want the user to be able to upload all of their past conversations and then get detailed analytics on them. At a latter stage I might also want to save their chats with their consent of course but for now I just want to build the web app that after uploading the past conversation with chatgpt will display interesting metrics. First of I want to display metrics the are easily computable like Average request per day, average conversation length, average requests in words, total number of requests, most number of request on one day… I also want to display metrics that use an LLM as a back bone to figure out the most touched topics, likely interests of the user, guesses on his/her profession and paint a likely picture of them with dalle. Help me turn this vision into a reality by first advising me on the tech stack. I want to build this app as fast as possible and want to use a v

'why is there a difference?: > # Initialize port...\n Write R code to accomplish the following task:...\nhow do you calculate the standard deviations\\n\\...\nIn what are should I get a hotel on my trip to ...\ndoes this work? weights_1 = c(0.4,0.2,0.4)\\n\\nw...\nermnos = c(39731,79089,83148)\\n\\nweights_1 = c(...\nexplain # Calculate daily average return and st...\nwhat are some impressive marketing campaigns an...\nexplain this code in depth: for (i in 1:2) {\\n\\...\nConsider the following three stocks with permno...\nexplain the cumulative product function in r an...\nerstelle mir ein podacast zu den themen der att...\nwhats wrong here: import numpy as np import pan...\nDrawing your conclusion which model is better o...\nI am currently studying in shenzhen for my exch...\nI am visiting Seoul for 4 days. I want to get a...\n correct this: ### Bias^2 Against Number of Tre...\ndoes it make sense that accuracy and auroc alwa...\nThe Auroc and accuracy always has the same valu...\ntra